In [103]:
import requests
import pandas as pd

url = "https://opensky-network.org/api/states/all"

from dotenv import load_dotenv

import os
from dotenv import load_dotenv, find_dotenv
load_dotenv(find_dotenv())

user = os.environ.get("user")
password = os.environ.get("password")

r = requests.get(url, auth=(user, password))

json_data = r.json()
states = pd.DataFrame(json_data['states'], columns=['icao24', 'callsign', 'origin_country', 'time_position', 
                                                    'last_contact', 'longitude', 'latitude', 'baro_altitude', 'on_ground', 'velocity', 
                                                    'true_track', 'vertical_rate', 'sensors', 'geo_altitude', 'squawk', 'spi', 'position_source'])
states.head()

200


icao24  callsign origin_country  time_position  last_contact  longitude  \
0  ab1644  UAL1926   United States   1.690156e+09    1690155511  -103.2513   
1  a5a8e2  N464EG    United States   1.690156e+09    1690155508  -122.9542   
2  aa56db  UAL587    United States   1.690156e+09    1690155511   -83.4430   
3  a1b2e3  N20858    United States   1.690155e+09    1690155377  -122.2486   
4  7c6b2d  JST811        Australia   1.690155e+09    1690155446   151.1802   

   latitude  baro_altitude  on_ground  velocity  true_track  vertical_rate  \
0   39.2846       10050.78      False    206.05       34.52          -0.33   
1   45.5406            NaN       True      0.00      323.44            NaN   
2   37.6239       10363.20      False    212.38      253.10           0.00   
3   38.2219         335.28      False     41.70        9.23          -2.28   
4  -33.9519            NaN       True      6.17      270.00            NaN   

  sensors  geo_altitude squawk    spi  position_source  
0    None      10675.62   7052  False                0  
1    None           NaN   None  False                0  
2    None      10774.68   2737  False                0  
3    None        289.56   None  False                0  
4    None           NaN   1170  False                0

In [104]:
states["roll"] = 0
states["yaw"] = -states["true_track"]
states["pitch"] = 90

In [116]:
# crteate a new column for the color 
# color should be a rgba list
# use a colormap from matplotlib
# map the origin_country column to the color column
# help me write a Python code to do this



import pandas as pd
import matplotlib.cm as cm

# Assuming you have the data in a pandas DataFrame called 'df'
# Replace 'origin_country' with the actual column name containing the countries

# Create a colormap from matplotlib
cmap = cm.get_cmap('viridis')  # You can choose any other colormap available in matplotlib

# Map origin_country to colors using the colormap
states['color'] = states['origin_country'].map(lambda country: tuple(int(c * 255) for c in cmap(hash(country))[:3]) + (255,))  # RGBA values with alpha=255

# 

states.head()


C:\Users\xif626\AppData\Local\Temp\ipykernel_29592\4122563868.py:16: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  cmap = cm.get_cmap('viridis')  # You can choose any other colormap available in matplotlib


icao24  callsign origin_country  time_position  last_contact  longitude  \
0  ab1644  UAL1926   United States   1.690156e+09    1690155511  -103.2513   
1  a5a8e2  N464EG    United States   1.690156e+09    1690155508  -122.9542   
2  aa56db  UAL587    United States   1.690156e+09    1690155511   -83.4430   
3  a1b2e3  N20858    United States   1.690155e+09    1690155377  -122.2486   
4  7c6b2d  JST811        Australia   1.690155e+09    1690155446   151.1802   

   latitude  baro_altitude  on_ground  velocity  ...  vertical_rate  sensors  \
0   39.2846       10050.78      False    206.05  ...          -0.33     None   
1   45.5406            NaN       True      0.00  ...            NaN     None   
2   37.6239       10363.20      False    212.38  ...           0.00     None   
3   38.2219         335.28      False     41.70  ...          -2.28     None   
4  -33.9519            NaN       True      6.17  ...            NaN     None   

  geo_altitude  squawk    spi  position_source  roll     yaw  pitch  \
0     10675.62    7052  False                0     0  -34.52     90   
1          NaN    None  False                0     0 -323.44     90   
2     10774.68    2737  False                0     0 -253.10     90   
3       289.56    None  False                0     0   -9.23     90   
4          NaN    1170  False                0     0 -270.00     90   

              color  
0  (68, 1, 84, 255)  
1  (68, 1, 84, 255)  
2  (68, 1, 84, 255)  
3  (68, 1, 84, 255)  
4  (68, 1, 84, 255)  

[5 rows x 21 columns]

In [119]:

import pandas as pd

from pydeck import Layer, Deck
from pydeck.data_utils import compute_view
from pydeck.types import String

# DATA_URL = "https://opensky-network.org/api/states/all"
SCENEGRAPH_URL = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/examples/scenegraph-layer/airplane.glb"

# Automatically fit viewport location based on data
# df = pd.read_json(DATA_URL)
# testjson = [
#             {"name": "test",
#              "coordinates" : [-83.7582848, 42.2739968],
#             },
#         ],
layer = Layer(
    type="ScenegraphLayer",
    id="scenegraph-layer",
    data=states,
    # pickable=True,
    scenegraph=SCENEGRAPH_URL,
    get_position=["longitude", "latitude", "geo_altitude"],
     sizeMinPixels=0.1,
      sizeMaxPixels=1.5,
    get_orientation= ["roll","yaw" , "pitch"],
    # set color
    get_color= "color",
    size_scale=500,
    # _animations={"*": {"speed": 5}},
    _lighting=String("pbr"),
)

# Render
# put china in the center of the map

view  = {"latitude": 35.8617, "longitude": 104.1954, "zoom": 3.5, "pitch": 0, "bearing": 0}
r = Deck(layer, 
        #  put China in the center
            initial_view_state=view,
        #  initial_view_state=view
         )


r.to_html("scenegraph_layer.html")